In [38]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns
import lightning as L
import torch
import torch.nn as nn
import torch.nn.functional as F
import yfinance as yf

import logging

# configure logging at the root level of Lightning
logging.getLogger("lightning.pytorch").setLevel(logging.ERROR)

%matplotlib inline
%load_ext tensorboard
sns.set_theme(context="paper", style="ticks", palette="tab10")

The tensorboard extension is already loaded. To reload it, use:
  %reload_ext tensorboard


In [6]:
train_size = 0.80 # train/test split
subsample = False # whether to randomly subsample the training data
subsample_size = 0.2 # fraction of training data to keep

# list of stock tickers to use, top 3 from S&P 500 sector by market cap
stock_tickers = ["META", "GOOGL", "NFLX", "AMZN", "TSLA", "HD", "PG", "COST", "PEP", "XOM", "CVX", "COP", "MA", "JPM", "V", "UNH", "JNJ", "LLY", "UNP", "BA", "CAT", "LIN", "SHW", "FCX", "PLD", "AMT", "EQIX", "MSFT", "AAPL", "AVGO", "NEE", "SO", "DUK"]

lookback_window = 30 # num of days to look back
lookahead_window = 1 # num of days to look ahead

input_size = 2 # num feature channels (price, volume, sentiment, etc)
num_layers = 8 # num of stacked LSTM layers
hidden_size = 64 # num of nodes per LSTM layer

max_epochs = 100 # max num of epochs to train for per ticker
learning_rate = 1e-4 # learning rate
batch_size = 256
shuffle_train = False
accelerator = "gpu"

In [7]:
class StockPricePredictor(L.LightningModule):
    def __init__(self,
                 input_size: int,
                 hidden_size: int,
                 num_layers: int,
                 output_size: int,
                 learning_rate: float,
                 train_losses: list[int],
                 test_losses: list[int]):
        super().__init__()
        self.lstm = nn.LSTM(input_size, hidden_size, num_layers, batch_first=True)
        self.linear = nn.Linear(hidden_size, output_size)
        self.train_losses = train_losses
        self.test_losses = test_losses
        self.learning_rate = learning_rate
    
    def forward(self, x: torch.Tensor):
        out, _ = self.lstm(x)
        out = self.linear(out[:, -1, :])
        return out
    
    def configure_optimizers(self):
        optimizer = torch.optim.Adam(self.parameters(), lr=self.learning_rate)
        return optimizer
    
    def training_step(self, batch, batch_idx):
        x, y = batch
        y_hat = self(x)
        loss = F.mse_loss(y_hat, y)
        self.log("train_loss", loss, on_epoch=True, on_step=True, prog_bar=False)
        return loss
    
    def validation_step(self, batch, batch_idx):
        x, y = batch
        y_hat = self(x)
        loss = F.mse_loss(y_hat, y)
        self.log("val_loss", loss, on_epoch=True, on_step=True, prog_bar=False)
        return loss
    
    def on_train_epoch_end(self):
        self.train_losses.append(self.trainer.callback_metrics["train_loss"].item())
        self.test_losses.append(self.trainer.callback_metrics["val_loss"].item())

In [8]:
import pickle as pkl

with open("../data/final/sp500-price-volume.pkl", "rb") as f:
    sp500_df = pkl.load(f)

with open("../data/final/sp500-price-volume-sentiment.pkl", "rb") as f:
    sp500_sentiment_df = pkl.load(f)

sp500_df["Ticker"] = sp500_df["Ticker"].astype("category")
sp500_df["Date"] = sp500_df["Date"].astype("datetime64[ns]")
sp500_df["Price"] = pd.to_numeric(sp500_df["Price"], errors="coerce", downcast="float")
sp500_df["Volume"] = pd.to_numeric(sp500_df["Volume"], errors="coerce", downcast="integer")

sp500_sentiment_df["Ticker"] = sp500_sentiment_df["Ticker"].astype("category")
sp500_sentiment_df["Date"] = sp500_sentiment_df["Date"].astype("datetime64[ns]")
sp500_sentiment_df["Sentiment"] = pd.to_numeric(sp500_sentiment_df["Sentiment"], errors="coerce", downcast="float")
sp500_sentiment_df["Price"] = pd.to_numeric(sp500_sentiment_df["Price"], errors="coerce", downcast="float")
sp500_sentiment_df["Volume"] = pd.to_numeric(sp500_sentiment_df["Volume"], errors="coerce", downcast="integer")

In [29]:
from sklearn.preprocessing import StandardScaler, MinMaxScaler

def split_data(df: pd.DataFrame,
               train_size: float = 0.8,
               lbp: int = 30,
               lfp: int = 1) -> tuple[np.ndarray, np.ndarray, np.ndarray, np.ndarray, StandardScaler]:
    """
    lbp: look back period
    lfp: look forward period
    """
    X_train = []
    y_train = []
    X_test = []
    y_test = []

    test_tickers = []

    tickers = df["Ticker"].unique()

    for ticker in tickers:
        ticker_df = df[df["Ticker"] == ticker]
        ticker_df = ticker_df.drop("Ticker", axis=1)
        ticker_df = ticker_df.set_index("Date")
        ticker_array = ticker_df.sort_index().values
        
        train_count = int(ticker_array.shape[0] * train_size)
        train = ticker_array[:train_count]
        test = ticker_array[train_count:]

        ticker_X_train = []
        ticker_y_train = []
        ticker_X_test = []
        ticker_y_test = []


        for i in range(lbp, train.shape[0] - lfp + 1):
            ticker_X_train.append(train[i - lbp:i, :])
            ticker_y_train.append(train[i:i + lfp, 0])
        
        for i in range(lbp, test.shape[0] - lfp + 1):
            ticker_X_test.append(test[i - lbp:i, :])
            ticker_y_test.append(test[i:i + lfp, 0])
            test_tickers.append(ticker)

        X_train.append(ticker_X_train)
        y_train.append(ticker_y_train)
        X_test.append(ticker_X_test)
        y_test.append(ticker_y_test)
    
    X_train = np.array(X_train)
    y_train = np.array(y_train)
    X_test = np.array(X_test)
    y_test = np.array(y_test)

    X_scaler = MinMaxScaler(feature_range=(0, 1))
    y_scaler = MinMaxScaler(feature_range=(0, 1))
    
    X_train = X_scaler.fit_transform(X_train.reshape(-1, X_train.shape[-1])).reshape(X_train.shape[0] * X_train.shape[1], X_train.shape[2], -1)
    X_test = X_scaler.transform(X_test.reshape(-1, X_test.shape[-1])).reshape(X_test.shape[0] * X_test.shape[1], X_test.shape[2], -1)
    y_train = y_scaler.fit_transform(y_train.reshape(-1, y_train.shape[-1])).reshape(y_train.shape[0] * y_train.shape[1], y_train.shape[2])
    y_test = y_scaler.transform(y_test.reshape(-1, y_test.shape[-1])).reshape(y_test.shape[0] * y_test.shape[1], y_test.shape[2])

    return X_train, y_train, X_test, y_test, y_scaler, test_tickers

(_, _, X_test_ns_15, y_test_15, _, test_tickers_15) = split_data(sp500_df, train_size=train_size, lbp=15, lfp=lookahead_window)
(_, _, X_test_s_15, _, _, _) = split_data(sp500_sentiment_df, train_size=train_size, lbp=15, lfp=lookahead_window)

(_, _, X_test_ns_30, y_test_30, _, test_tickers_30) = split_data(sp500_df, train_size=train_size, lbp=30, lfp=lookahead_window)
(_, _, X_test_s_30, _, _, _) = split_data(sp500_sentiment_df, train_size=train_size, lbp=30, lfp=lookahead_window)

(_, _, X_test_ns_60, y_test_60, _, test_tickers_60) = split_data(sp500_df, train_size=train_size, lbp=60, lfp=lookahead_window)
(_, _, X_test_s_60, _, _, _) = split_data(sp500_sentiment_df, train_size=train_size, lbp=60, lfp=lookahead_window)

(_, _, X_test_ns_90, y_test_90, _, test_tickers_90) = split_data(sp500_df, train_size=train_size, lbp=90, lfp=lookahead_window)
(_, _, X_test_s_90, _, _, _) = split_data(sp500_sentiment_df, train_size=train_size, lbp=90, lfp=lookahead_window)

print(f"X_test_ns_15: {X_test_ns_15.shape}")
print(f"X_test_s_15: {X_test_s_15.shape}")
print(f"y_test_15: {y_test_15.shape}")
print()
print(f"X_test_ns_30: {X_test_ns_30.shape}")
print(f"X_test_s_30: {X_test_s_30.shape}")
print(f"y_test_30: {y_test_30.shape}")
print()
print(f"X_test_ns_60: {X_test_ns_60.shape}")
print(f"X_test_s_60: {X_test_s_60.shape}")
print(f"y_test_60: {y_test_60.shape}")
print()
print(f"X_test_ns_90: {X_test_ns_90.shape}")
print(f"X_test_s_90: {X_test_s_90.shape}")
print(f"y_test_90: {y_test_90.shape}")

X_test_ns_15: (16137, 15, 2)
X_test_s_15: (16137, 15, 3)
y_test_15: (16137, 1)

X_test_ns_30: (15642, 30, 2)
X_test_s_30: (15642, 30, 3)
y_test_30: (15642, 1)

X_test_ns_60: (14652, 60, 2)
X_test_s_60: (14652, 60, 3)
y_test_60: (14652, 1)

X_test_ns_90: (13662, 90, 2)
X_test_s_90: (13662, 90, 3)
y_test_90: (13662, 1)


In [31]:
test_tickers_15 = np.array(test_tickers_15, dtype="str")
test_tickers_30 = np.array(test_tickers_30, dtype="str")
test_tickers_60 = np.array(test_tickers_60, dtype="str")
test_tickers_90 = np.array(test_tickers_90, dtype="str")

In [10]:
with open(f"./final/lookback-15/no-sentiment-model.pkl", "rb") as f:
    model_ns_15 = pkl.load(f)

with open(f"./final/lookback-15/sentiment-model.pkl", "rb") as f:
    model_s_15 = pkl.load(f)

with open(f"./final/lookback-30/no-sentiment-model.pkl", "rb") as f:
    model_ns_30 = pkl.load(f)

with open(f"./final/lookback-30/sentiment-model.pkl", "rb") as f:
    model_s_30 = pkl.load(f)

with open(f"./final/lookback-60/no-sentiment-model.pkl", "rb") as f:
    model_ns_60 = pkl.load(f)

with open(f"./final/lookback-60/sentiment-model.pkl", "rb") as f:
    model_s_60 = pkl.load(f)

with open(f"./final/lookback-90/no-sentiment-model.pkl", "rb") as f:
    model_ns_90 = pkl.load(f)

with open(f"./final/lookback-90/sentiment-model.pkl", "rb") as f:
    model_s_90 = pkl.load(f)

model_ns_15.eval()
model_s_15.eval()
model_ns_30.eval()
model_s_30.eval()
model_ns_60.eval()
model_s_60.eval()
model_ns_90.eval()
model_s_90.eval()

StockPricePredictor(
  (lstm): LSTM(3, 32, num_layers=4, batch_first=True)
  (linear): Linear(in_features=32, out_features=1, bias=True)
)

In [21]:
y_hat_ns_15 = model_ns_15(torch.from_numpy(X_test_ns_15).float()).detach().numpy()
y_hat_s_15 = model_s_15(torch.from_numpy(X_test_s_15).float()).detach().numpy()

y_hat_ns_30 = model_ns_30(torch.from_numpy(X_test_ns_30).float()).detach().numpy()
y_hat_s_30 = model_s_30(torch.from_numpy(X_test_s_30).float()).detach().numpy()

y_hat_ns_60 = model_ns_60(torch.from_numpy(X_test_ns_60).float()).detach().numpy()
y_hat_s_60 = model_s_60(torch.from_numpy(X_test_s_60).float()).detach().numpy()

y_hat_ns_90 = model_ns_90(torch.from_numpy(X_test_ns_90).float()).detach().numpy()
y_hat_s_90 = model_s_90(torch.from_numpy(X_test_s_90).float()).detach().numpy()

In [82]:
sns.color_palette("tab10")

[(0.12156862745098039, 0.4666666666666667, 0.7058823529411765),
 (1.0, 0.4980392156862745, 0.054901960784313725),
 (0.17254901960784313, 0.6274509803921569, 0.17254901960784313),
 (0.8392156862745098, 0.15294117647058825, 0.1568627450980392),
 (0.5803921568627451, 0.403921568627451, 0.7411764705882353),
 (0.5490196078431373, 0.33725490196078434, 0.29411764705882354),
 (0.8901960784313725, 0.4666666666666667, 0.7607843137254902),
 (0.4980392156862745, 0.4980392156862745, 0.4980392156862745),
 (0.7372549019607844, 0.7411764705882353, 0.13333333333333333),
 (0.09019607843137255, 0.7450980392156863, 0.8117647058823529)]

In [123]:
fig, ax = plt.subplots(6, 1, figsize=(12, 12), dpi=900)
ax = ax.flatten()
sns.despine()

firm_1 = "AAPL"
firm_2 = "NFLX"
firm_3 = "AVGO"
firm_4 = "MSFT"
firm_5 = "AMZN"
firm_6 = "COST"

sns.lineplot(y_hat_ns_90[test_tickers_90 == firm_1, 0], label="Predicted Price (No Sentiment)", ax=ax[0])
sns.lineplot(y_hat_s_90[test_tickers_90 == firm_1, 0], label="Predicted Price (With Sentiment)", ax=ax[0])
sns.lineplot(y_test_90[test_tickers_90 == firm_1, 0], label="Actual Price", ax=ax[0])

sns.lineplot(y_hat_ns_90[test_tickers_90 == firm_2, 0], label="Predicted Price (No Sentiment)", ax=ax[1])
sns.lineplot(y_hat_s_90[test_tickers_90 == firm_2, 0], label="Predicted Price (With Sentiment)", ax=ax[1])
sns.lineplot(y_test_90[test_tickers_90 == firm_2, 0], label="Actual Price", ax=ax[1])

sns.lineplot(y_hat_ns_90[test_tickers_90 == firm_3, 0], label="Predicted Price (No Sentiment)", ax=ax[2])
sns.lineplot(y_hat_s_90[test_tickers_90 == firm_3, 0], label="Predicted Price (With Sentiment)", ax=ax[2])
sns.lineplot(y_test_90[test_tickers_90 == firm_3, 0], label="Actual Price", ax=ax[2])

sns.lineplot(y_hat_ns_90[test_tickers_90 == firm_4, 0], label="Predicted Price (No Sentiment)", ax=ax[3])
sns.lineplot(y_hat_s_90[test_tickers_90 == firm_4, 0], label="Predicted Price (With Sentiment)", ax=ax[3])
sns.lineplot(y_test_90[test_tickers_90 == firm_4, 0], label="Actual Price", ax=ax[3])

sns.lineplot(y_hat_ns_90[test_tickers_90 == firm_5, 0], label="Predicted Price (No Sentiment)", ax=ax[4])
sns.lineplot(y_hat_s_90[test_tickers_90 == firm_5, 0], label="Predicted Price (With Sentiment)", ax=ax[4])
sns.lineplot(y_test_90[test_tickers_90 == firm_5, 0], label="Actual Price", ax=ax[4])

sns.lineplot(y_hat_ns_90[test_tickers_90 == firm_6, 0], label="Predicted Price (No Sentiment)", ax=ax[5])
sns.lineplot(y_hat_s_90[test_tickers_90 == firm_6, 0], label="Predicted Price (With Sentiment)", ax=ax[5])
sns.lineplot(y_test_90[test_tickers_90 == firm_6, 0], label="Actual Price", ax=ax[5])

# ax[0].set_title(firm_1)
# ax[1].set_title(firm_2)
# ax[2].set_title(firm_3)
# ax[3].set_title(firm_4)
# ax[4].set_title(firm_4)
ax[5].set_xlabel("Days")
ax[0].set_ylabel("Price")
ax[1].set_ylabel("Price")
ax[2].set_ylabel("Price")
ax[3].set_ylabel("Price")
ax[4].set_ylabel("Price")
ax[5].set_ylabel("Price")

# for a in ax:
#     a.get_legend().remove()

Text(0, 0.5, 'Price')